In [64]:
import requests
import sqlite3
import time
import json

# API base URL
BASE_URL = "https://api.www.sbir.gov/public/api/solicitations"

# Database setup
DB_NAME = "solicitations.db"

# Function to create the database tables
def setup_database():
    conn = sqlite3.connect(DB_NAME)
    cursor = conn.cursor()
    
    # Create solicitations table
    cursor.execute("""
        CREATE TABLE IF NOT EXISTS solicitations (
            solicitation_id INTEGER PRIMARY KEY,
            solicitation_title TEXT,
            solicitation_number TEXT UNIQUE,
            program TEXT,
            phase TEXT,
            agency TEXT,
            branch TEXT,
            solicitation_year INTEGER,
            release_date TEXT,
            open_date TEXT,
            close_date TEXT,
            application_due_dates TEXT,
            solicitation_agency_url TEXT,
            current_status TEXT
        )
    """)
    
    # Create topics table (Only if more than one exists per solicitation)
    cursor.execute("""
        CREATE TABLE IF NOT EXISTS topics (
            topic_number TEXT,
            solicitation_id INTEGER,
            topic_title TEXT,
            branch TEXT,
            topic_description TEXT,
            sbir_topic_link TEXT,
            topic_open_date TEXT,
            topic_closed_date TEXT,
            PRIMARY KEY (topic_number, solicitation_id),
            FOREIGN KEY (solicitation_id) REFERENCES solicitations(solicitation_id)
        )
    """)

    # Create subtopics table linked to topics
    cursor.execute("""
        CREATE TABLE IF NOT EXISTS subtopics (
            subtopic_id INTEGER PRIMARY KEY,
            subtopic_number TEXT,
            topic_number TEXT,
            solicitation_id INTEGER,
            subtopic_title TEXT,
            branch TEXT,
            subtopic_description TEXT,
            subtopic_open_date TEXT,
            subtopic_close_date TEXT,
            FOREIGN KEY (topic_number, solicitation_id) REFERENCES topics(topic_number, solicitation_id)
        )
    """)

    conn.commit()
    conn.close()

# Function to fetch data from API
def fetch_data(page):
    params = {
        "rows": 50,
        "start": page * 50,
        #"open": 1,
        #"agency": "HHS",
        #"keyword": "xyz"
        }
    response = requests.get(BASE_URL, params=params)
    if response.status_code == 200:
        return response.json()
    else:
        print(f"Error fetching page {page}: {response.status_code}")
        return None

# Function to insert data into SQLite database
def insert_data(data):
    conn = sqlite3.connect(DB_NAME)
    cursor = conn.cursor()
    
    for item in data:
        # Insert into solicitations table
        cursor.execute("""
            INSERT OR REPLACE INTO solicitations (
                solicitation_id, solicitation_title, solicitation_number, program, phase, agency, branch,
                solicitation_year, release_date, open_date, close_date, application_due_dates,
                solicitation_agency_url, current_status
            ) VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
        """, (
            item.get("solicitation_id"),
            item.get("solicitation_title"),
            item.get("solicitation_number"),
            item.get("program"),
            item.get("phase"),
            item.get("agency"),
            item.get("branch"),
            item.get("solicitation_year"),
            item.get("release_date"),
            item.get("open_date"),
            item.get("close_date"),
            json.dumps(item.get("application_due_date")),  # Store as JSON string
            item.get("solicitation_agency_url"),
            item.get("current_status")
        ))

        topics = item.get("solicitation_topics", [])
        if topics and isinstance(topics, list):  # Check if topics exists and is a list
            for topic in topics:
                if topic:
                    cursor.execute("""
                        INSERT OR REPLACE INTO topics (
                            topic_number, solicitation_id, topic_title, topic_description, topic_open_date, topic_closed_date
                        ) VALUES (?, ?, ?, ?, ?, ?)
                    """, (
                        topic.get("topic_number"),
                        item.get("solicitation_id"),
                        topic.get("topic_title"),
                        topic.get("topic_description"),
                        topic.get("topic_open_date"),
                        topic.get("topic_closed_date")
                    ))

                # Insert subtopics only if they exist
                subtopics = topic.get("subtopics", [])
                if subtopics and isinstance(subtopics, list):
                    for subtopic in subtopics:
                        if subtopic and subtopic.get("subtopic_id"):
                            try:
                                cursor.execute("""
                                    INSERT OR REPLACE INTO subtopics (
                                        subtopic_id, subtopic_number, topic_number, solicitation_id, subtopic_title, branch, subtopic_description, subtopic_open_date, subtopic_close_date
                                    ) VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?)
                                """, (
                                    subtopic.get("subtopic_id"),
                                    subtopic.get("subtopic_number"),
                                    topic.get("topic_number"),  # This is the foreign key
                                    item.get("solicitation_id"),
                                    subtopic.get("subtopic_title"),
                                    subtopic.get("branch"),
                                    subtopic.get("subtopic_description"),
                                    subtopic.get("subtopic_open_date"),
                                    subtopic.get("subtopic_close_date"),
                                ))
                            except sqlite3.Error as e:
                                print(f"Error inserting subtopic {subtopic.get('subtopic_number')}: {e}")
                                print(f"Topic number was: {topic.get('topic_number')}")

    conn.commit()
    conn.close()

# Main execution
def main():
    setup_database()
    
    for page in range(3):  #number of pages
        print(f"Fetching page {page + 1}...")
        data = fetch_data(page)
        if data:
            insert_data(data)
        else:
            print("No more data")
            break
        time.sleep(1)  # Avoid excessive requests

    print("Data successfully stored in SQLite database.")

if __name__ == "__main__":
    main()


Fetching page 1...
Fetching page 2...
Fetching page 3...
  - Processing subtopic: Z10.01 - Cryogenic Fluid Management
  - Processing subtopic: Z10.05 - Rotating Detonation Rocket Engine Nozzles and Instrumentation
  - Processing subtopic: S13.06 - Dynamic Power Conversion
  - Processing subtopic: Z1.05 - Lunar and Planetary Surface Power Management and Distribution
  - Processing subtopic: Z1.09 - Energy Storage for the Lunar/Mars Surface
  - Processing subtopic: H15.01 - Autonomous Capabilities for Lunar Surface Mobility Systems
  - Processing subtopic: H6.22 - Deep Neural Net and Neuromorphic Processors for In-Space Autonomy andCognition
  - Processing subtopic: S17.03 - Fault Management Technologies
  - Processing subtopic: S13.01 - Robotic Mobility, Manipulation, and Sampling
  - Processing subtopic: Z14.01 - Lunar Surface Excavation
  - Processing subtopic: Z14.03 - Assembly and Outfitting of Tall Truss-Based Power Towers
  - Processing subtopic: Z5.06 - Servicing and Assembly App

In [65]:
def check_schema():
    conn = sqlite3.connect(DB_NAME)
    cursor = conn.cursor()
    
    cursor.execute("SELECT sql FROM sqlite_master WHERE type='table' AND name='topics'")
    print("\nTopics table schema:")
    print(cursor.fetchone()[0])
    
    cursor.execute("SELECT sql FROM sqlite_master WHERE type='table' AND name='subtopics'")
    print("\nSubtopics table schema:")
    print(cursor.fetchone()[0])
    
    conn.close()

def fetch_solicitations():
    conn = sqlite3.connect(DB_NAME)
    cursor = conn.cursor()
    
    cursor.execute("SELECT * FROM solicitations") # LIMIT 10")
    rows = cursor.fetchall()
    
    for row in rows:
        print(row)
    
    conn.close()

def fetch_topics():
    conn = sqlite3.connect(DB_NAME)
    cursor = conn.cursor()
    
    cursor.execute("SELECT * FROM topics") # LIMIT 10")
    rows = cursor.fetchall()
    
    for row in rows:
        print(row)
    
    conn.close()

def fetch_subtopics():
    conn = sqlite3.connect(DB_NAME)
    cursor = conn.cursor()
    
    cursor.execute("SELECT * FROM subtopics") # LIMIT 10")
    rows = cursor.fetchall()

    for row in rows:
        print(row)
    
    conn.close()

def count_entries():
    conn = sqlite3.connect(DB_NAME)
    cursor = conn.cursor()
    
    # Count entries in solicitations table
    cursor.execute("SELECT COUNT(*) FROM solicitations")
    solicitation_count = cursor.fetchone()[0]
    
    # Count entries in topics table
    cursor.execute("SELECT COUNT(*) FROM topics")
    topic_count = cursor.fetchone()[0]

    cursor.execute("SELECT COUNT(*) FROM subtopics")
    subtopic_count = cursor.fetchone()[0]
    
    conn.close()
    
    return {
        "solicitations": solicitation_count,
        "topics": topic_count,
        "subtopics": subtopic_count
    }

if __name__ == "__main__":
    check_schema()
    
    print("Solicitations:")
    fetch_solicitations()
    
    print("\nTopics:")
    fetch_topics()

    print("\nSubtopics:")
    fetch_subtopics()

    counts = count_entries()
    print(f"Number of solicitations: {counts['solicitations']}")
    print(f"Number of topics: {counts['topics']}")
    print(f"Number of subtopics: {counts['subtopics']}")


Topics table schema:
CREATE TABLE topics (
            topic_number TEXT,
            solicitation_id INTEGER,
            topic_title TEXT,
            branch TEXT,
            topic_description TEXT,
            sbir_topic_link TEXT,
            topic_open_date TEXT,
            topic_closed_date TEXT,
            PRIMARY KEY (topic_number, solicitation_id),
            FOREIGN KEY (solicitation_id) REFERENCES solicitations(solicitation_id)
        )

Subtopics table schema:
CREATE TABLE subtopics (
            subtopic_id INTEGER PRIMARY KEY,
            subtopic_number TEXT,
            topic_number TEXT,
            solicitation_id INTEGER,
            subtopic_title TEXT,
            branch TEXT,
            subtopic_description TEXT,
            subtopic_open_date TEXT,
            subtopic_close_date TEXT,
            FOREIGN KEY (topic_number, solicitation_id) REFERENCES topics(topic_number, solicitation_id)
        )
Solicitations:
(925, 'NIAID SBIR Phase II Clinical Trial I

In [50]:
def count_dod_topics():
    conn = sqlite3.connect(DB_NAME)
    cursor = conn.cursor()
    
    # Get DOD topics with close date after 2025/02/18
    cursor.execute("""
        SELECT t.* 
        FROM topics t
        JOIN solicitations s ON t.solicitation_id = s.solicitation_id 
        WHERE s.agency = 'DOD'
        AND t.topic_closed_date > '2025/02/18'
    """)
    
    rows = cursor.fetchall()
    
    print(f"\nFound {len(rows)} DOD topics closing after 2025/02/18:")
    for row in rows:
        print(row)
    
    conn.close()
    
    return len(rows)

if __name__ == "__main__":
    count_dod_topics()


Found 32 DOD topics closing after 2025/02/18:
('A254-010', 1220, 'Radar Signal Processing Improvements for Probability of Detection', 'ARMY', 'OUSD (R&E) CRITICAL TECHNOLOGY AREA(S): Integrated Sensing and Cyber; Advanced Computing and Software\n\nOBJECTIVE: Current ground-based radar systems cannot meet the detection needs of evolving longer range threat systems without sacrificing scan times. The Army needs a solution, such as novel signal processing techniques, that can be implemented on existing radars that will provide improvements in probability of detection at longer ranges. Solutions must not impact current scan time requirements.\n\nDESCRIPTION: U.S. Army, Navy, and Air Force radar systems must effectively counter emerging threats. It is desirable to update existing radar systems to detect emerging long-range threats. Particularly, counterfire target acquisition (CTA) radars must detect emerging surface-launched projectile threats at further ranges. Typical methods to improve